In [ ]:
!pip install torch

  Using cached nvidia_cuda_nvrtc_cu12-12.1.105-py3-none-manylinux1_x86_64.whl.metadata (1.5 kB)
  Using cached nvidia_cuda_runtime_cu12-12.1.105-py3-none-manylinux1_x86_64.whl.metadata (1.5 kB)
  Using cached nvidia_cuda_cupti_cu12-12.1.105-py3-none-manylinux1_x86_64.whl.metadata (1.6 kB)
  Using cached nvidia_cudnn_cu12-8.9.2.26-py3-none-manylinux1_x86_64.whl.metadata (1.6 kB)
  Using cached nvidia_cublas_cu12-12.1.3.1-py3-none-manylinux1_x86_64.whl.metadata (1.5 kB)
  Using cached nvidia_cufft_cu12-11.0.2.54-py3-none-manylinux1_x86_64.whl.metadata (1.5 kB)
  Using cached nvidia_curand_cu12-10.3.2.106-py3-none-manylinux1_x86_64.whl.metadata (1.5 kB)
  Using cached nvidia_cusolver_cu12-11.4.5.107-py3-none-manylinux1_x86_64.whl.metadata (1.6 kB)
  Using cached nvidia_cusparse_cu12-12.1.0.106-py3-none-manylinux1_x86_64.whl.metadata (1.6 kB)
  Using cached nvidia_nccl_cu12-2.20.5-py3-none-manylinux2014_x86_64.whl.metadata (1.8 kB)
  Using cached nvidia_nvtx_cu12-12.1.105-py3-none-manylinu

In [ ]:
!pip install transformers[torch]

In [ ]:
!pip install accelerate -U

   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 315.1/315.1 kB 21.3 MB/s eta 0:00:00
  Attempting uninstall: accelerate
    Found existing installation: accelerate 0.32.1
    Uninstalling accelerate-0.32.1:
      Successfully uninstalled accelerate-0.32.1


In [ ]:
!pip install datasets

   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 547.8/547.8 kB 29.3 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 116.3/116.3 kB 10.9 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 316.1/316.1 kB 27.1 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 39.9/39.9 MB 57.6 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 64.9/64.9 kB 5.7 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 134.8/134.8 kB 13.3 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 194.1/194.1 kB 16.7 MB/s eta 0:00:00
  Attempting uninstall: requests
    Found existing installation: requests 2.31.0
    Uninstalling requests-2.31.0:
      Successfully uninstalled requests-2.31.0
  Attempting uninstall: pyarrow
    Found existing installation: pyarrow 14.0.2
    Uninstalling pyarrow-14.0.2:
      Successfully uninstalled pyarrow-14.0.2
  Attempting uninstall: fsspec
    Found existing installation: fsspec 2024.6.1
    Uninstalling fsspec-2024.6.1:
  

# Get Data

In [ ]:
import pandas as pd
from sklearn.model_selection import train_test_split
from transformers import BertTokenizer, BertForSequenceClassification, TrainingArguments, Trainer
from datasets import Dataset

In [ ]:
ChatGPT=pd.read_csv("/content/drive/MyDrive/SDGs/Data/ChatGPT/ChatGPT_Generated_Articles05052024.csv")
OSDG=pd.read_csv("/content/drive/MyDrive/SDGs/Data/OSDG_Translated1303.csv",sep="\t",encoding="utf-8")

In [ ]:
##Decision to use agreement >=0.7
OSDG=OSDG[OSDG['agreement']>=0.7]

In [ ]:
len(OSDG)

22030

In [ ]:
OSDG=OSDG[['Translation','sdg']].rename(columns={'Translation':'text'})

In [ ]:
OSDG['Source']="OSDG"

In [ ]:
OSDG.head(10)

text  sdg Source
0   ومن منظور النوع الاجتماعي، يشير بولجارد إلى أن...    5   OSDG
2   ويخفي الرقم المتوسط أيضًا اختلافات كبيرة بين م...    3   OSDG
8   تقوم محطة الأبحاث الأوقيانوغرافية والليمنية ال...    6   OSDG
9   ناقشت الفصول السابقة سبل جعل النظم الغذائية أك...    2   OSDG
11  &quot;الحرب على الإرهاب&quot; وإطار القانون ال...   16   OSDG
13  ويبدو أن معدلات الوصفات الطبية أعلى عندما تكون...    8   OSDG
14  وعلى النقيض من ذلك، ظلت حصة الأسر في سن العمل ...    5   OSDG
15  يدفع الآباء الحد الأقصى لرسوم رياض الأطفال فقط...    4   OSDG
16  وهي لا تشمل الأنشطة التي يتم فيها توجيه الدعم ...   13   OSDG
19  وبالنسبة لهؤلاء الأفراد، تبلغ النفقات النثرية ...    3   OSDG

In [ ]:
OSDG['text']=OSDG.text.str.replace("&quot;", "")

## Final Data

In [ ]:
Final_Data=pd.concat([ChatGPT,OSDG])

In [ ]:
Final_Data.sample(10)

sdg                                               text   Source
4153     6  الإجراءات الموصى بها في المجال (2) ثم (3) مشرو...     OSDG
7291     3  تنجم إخفاقات السوق عن عدم تماثل المعلومات بين ...     OSDG
34005    6  غالبًا ما تبين أن مشاريع إعادة التوطين السابقة...     OSDG
20549    9  وفي المقابل، ظل التمويل الميسر الموجه نحو التك...     OSDG
24681   13  وصعد الأمين العام إلى المنصة ليعرب عن أسفه لعد...     OSDG
3720     0  قام المعهد الوطني للأبحاث الفلكية والجيوفيزيائ...  ChatGPT
7103     0  تحولت معالم مدينة دبي لتكون واحدة من أهم الموا...  ChatGPT
13534    4  هل ستجعل التدريس والتعلم أكثر فعالية وأكثر أهم...     OSDG
21130    3  إن التحول النموذجي من التركيز الأكثر تحديداً ل...     OSDG
6259     0  على الرغم من الظروف الاقتصادية الصعبة التي شهد...  ChatGPT

In [ ]:
duplicates = Final_Data.duplicated(subset=['text'],keep=False)

In [ ]:
Final_Data[duplicates] # 3 duplicates all from OSDG

sdg                                               text Source
7045    16  ويستكشف هذا الفصل التفاعل بين قمع الإرهاب والق...   OSDG
10993    9  ولكن في الوقت نفسه، يمكنها تعزيز الابتكار من خ...   OSDG
30544    4  واستنادًا إلى قاعدة المعرفة الكبيرة المتعلقة ب...   OSDG
30957    9  ولكن في الوقت نفسه، يمكنها تعزيز الابتكار من خ...   OSDG
34789    4  واستنادًا إلى قاعدة المعرفة الكبيرة المتعلقة ب...   OSDG
35738   16  ويستكشف هذا الفصل التفاعل بين قمع الإرهاب والق...   OSDG

### Binary Data

In [ ]:
Final_Data['sdg_binary']=Final_Data['sdg'].apply(lambda x: 1 if x >0 else 0)

In [ ]:
Final_Data.sample(10)

sdg                                               text   Source  \
773      4  يهدف المشرفون إلى زيارة المدارس والإشراف على س...     OSDG   
12682    2  ومن الأمثلة الممتازة على هذا النهج برنامج Top ...     OSDG   
3375     0  في أحدث الدراسات العلمية، كشفت مجموعة من الباح...  ChatGPT   
38982    3  ويمهد التشريع الذي تمت الموافقة عليه في يونيو/...     OSDG   
26532    1  الكيريكيري هو شكل من أشكال المعاملة بالمثل حيث...     OSDG   
2726    13  تستعد الأمم المتحدة لتنظيم مؤتمر جديد بشأن الق...  ChatGPT   
6595     3  ومع ذلك، تم تطبيق معدل الخصوبة الإجمالي على 16...     OSDG   
2071     7  وفي غياب مدفوعات الندرة الشديدة أو مدفوعات الط...     OSDG   
3753     0  يستمر النقاش الواسع بين الساسة والمستثمرين في ...  ChatGPT   
16901    9  وقد تم دعم هذه الأحداث من قبل شركات خاصة، بما ...     OSDG   

       sdg_binary  
773             1  
12682           1  
3375            0  
38982           1  
26532           1  
2726            1  
6595            1  
2071            1  
3753            0  
16901           1

In [ ]:
Final_Data.sdg_binary.value_counts(normalize=True)*100

sdg_binary
1    86.074874
0    13.925126
Name: proportion, dtype: float64

In [ ]:
Final_Data[Final_Data['sdg_binary']==1].Source.value_counts(normalize=True)*100

Source
OSDG       86.947942
ChatGPT    13.052058
Name: proportion, dtype: float64

# Training

## Binary

### Data Split and undersampling

In [ ]:
import pandas as pd
from sklearn.model_selection import train_test_split
from sklearn.utils import resample, shuffle


# Step 1: Data Splitting and Undersampling for Binary Classification (SDG vs. Non-SDG)

# Split the dataset into features (text) and labels (SDG)
X = Final_Data['text']
y = Final_Data['sdg_binary']
S= Final_Data['Source']


# Split the data into train, validation, and test sets
X_train_val, X_val_test, y_train_val, y_val_test, S_train_val, S_val_test = train_test_split(X, y, S, test_size=0.15, random_state=42, stratify=y)

# Undersample the majority class (SDG) in the training set
X_train_sdg_OSDG = X_train_val[(y_train_val == 1) & (S_train_val=='OSDG')]  # SDG-related texts
X_train_sdg_ChatGPT = X_train_val[(y_train_val == 1) & (S_train_val=='ChatGPT')]

X_train_non_sdg = X_train_val[y_train_val == 0]  # Non-SDG texts

# Determine the number of samples to keep for undersampling
#num_samples = min(len(X_train_sdg), len(X_train_non_sdg))
num_samples = min(len(X_train_sdg_OSDG)+len(X_train_sdg_ChatGPT), len(X_train_non_sdg))


# Undersample the majority class (SDG) to match the number of samples in the minority class (Non-SDG)
#X_train_sdg_downsampled = resample(X_train_sdg, replace=False, n_samples=num_samples, random_state=42)

X_train_sdg_OSDG_downsampled = resample(X_train_sdg_OSDG, replace=False, n_samples=int(num_samples/2), random_state=42)
X_train_sdg_ChatGPT_downsampled = resample(X_train_sdg_ChatGPT, replace=False, n_samples=int(num_samples/2), random_state=42)

X_train_sdg_downsampled=pd.concat([X_train_sdg_OSDG_downsampled, X_train_sdg_ChatGPT_downsampled], axis=0)


# Combine the downsampled SDG-related texts with the Non-SDG texts
X_train_downsampled = pd.concat([X_train_sdg_downsampled, X_train_non_sdg], axis=0)
y_train_downsampled = pd.concat([pd.Series([1]*num_samples), pd.Series([0]*num_samples)], axis=0)

# Shuffle the downsampled data
X_train_downsampled, y_train_downsampled = shuffle(X_train_downsampled, y_train_downsampled, random_state=42)

##Create val and test sets
X_val, X_test, y_val, y_test = train_test_split(X_val_test, y_val_test, test_size=0.5, random_state=42, stratify=y_val_test)



In [ ]:
#@title Simple undersamplin working

import pandas as pd
from sklearn.model_selection import train_test_split
from sklearn.utils import resample, shuffle
# Load your dataset (assuming it's stored in a DataFrame named Final_Data)
# Example:
# Final_Data = pd.read_csv("your_dataset.csv")

# Step 1: Data Splitting and Undersampling for Binary Classification (SDG vs. Non-SDG)

# Split the dataset into features (text) and labels (SDG)
X = Final_Data['text']
y = Final_Data['sdg_binary']

# Split the data into train, validation, and test sets
X_train_val, X_val_test, y_train_val, y_val_test = train_test_split(X, y, test_size=0.15, random_state=42, stratify=y)

# Undersample the majority class (SDG) in the training set
X_train_sdg = X_train_val[y_train_val == 1]  # SDG-related texts
X_train_non_sdg = X_train_val[y_train_val == 0]  # Non-SDG texts

# Determine the number of samples to keep for undersampling
num_samples = min(len(X_train_sdg), len(X_train_non_sdg))

# Undersample the majority class (SDG) to match the number of samples in the minority class (Non-SDG)
X_train_sdg_downsampled = resample(X_train_sdg, replace=False, n_samples=num_samples, random_state=42)

# Combine the downsampled SDG-related texts with the Non-SDG texts
X_train_downsampled = pd.concat([X_train_sdg_downsampled, X_train_non_sdg], axis=0)
y_train_downsampled = pd.concat([pd.Series([1]*num_samples), pd.Series([0]*num_samples)], axis=0)

# Shuffle the downsampled data
X_train_downsampled, y_train_downsampled = shuffle(X_train_downsampled, y_train_downsampled, random_state=42)

##Create val and test sets
X_val, X_test, y_val, y_test = train_test_split(X_val_test, y_val_test, test_size=0.5, random_state=42, stratify=y_val_test)




In [ ]:
y_train_val.value_counts(normalize=True)*100

sdg_binary
1    86.07514
0    13.92486
Name: proportion, dtype: float64

In [ ]:
y_train_downsampled.value_counts(normalize=True)*100

0    50.0
1    50.0
Name: proportion, dtype: float64

In [ ]:
y_test.value_counts(normalize=True)*100

sdg_binary
1    86.050725
0    13.949275
Name: proportion, dtype: float64

### Training model

#### BERT

In [ ]:
!rm -r "/content/outputs"

In [ ]:


# Initialize the BERT tokenizer
tokenizer = BertTokenizer.from_pretrained("UBC-NLP/ARBERTv2",model_max_length=512)

# # Tokenize texts and calculate number of tokens per text
# token_lengths = []
# for text in X_train_downsampled:
#     tokens = tokenizer.encode(text, add_special_tokens=True)
#     token_lengths.append(len(tokens))

# Calculate average number of tokens per text
# average_tokens = sum(token_lengths) / len(token_lengths)
# print(f"Average number of tokens per text: {average_tokens:.2f}")

# Convert labels to numerical values
# label_dict = {label: i for i, label in enumerate(Final_Data['sdg'].unique())}
# Final_Data['sdg'] = Final_Data['sdg'].map(label_dict)

# Split the data into training, validation, and test sets
# train_texts, val_test_texts, train_labels, val_test_labels = train_test_split(Final_Data['text'], Final_Data['sdg'], test_size=0.2, random_state=42, stratify=Final_Data['sdg'])
# val_texts, test_texts, val_labels, test_labels = train_test_split(val_test_texts, val_test_labels, test_size=0.5, random_state=42, stratify=val_test_labels)

# Tokenize the texts
train_encodings = tokenizer(X_train_downsampled.tolist(), truncation=True, padding=True, max_length=512)
val_encodings = tokenizer(X_val.tolist(), truncation=True, padding=True, max_length=512)
test_encodings = tokenizer(X_test.tolist(), truncation=True, padding=True, max_length=512)

# Create datasets
# train_dataset = Dataset.from_dict({key: val for key, val in train_encodings.items()}, labels=y_train_downsampled.tolist())
# val_dataset = Dataset.from_dict({key: val for key, val in val_encodings.items()}, labels= y_val.tolist())
# test_dataset = Dataset.from_dict({key: val for key, val in test_encodings.items()}, labels= y_test.tolist())

# Create the training dataset
train_dataset = Dataset.from_dict({"input_ids": train_encodings["input_ids"],
                                    "attention_mask": train_encodings["attention_mask"],
                                    "labels": y_train_downsampled.tolist()})

# Create the validation dataset
val_dataset = Dataset.from_dict({"input_ids": val_encodings["input_ids"],
                                  "attention_mask": val_encodings["attention_mask"],
                                  "labels": y_val.tolist()})

test_dataset = Dataset.from_dict({"input_ids": test_encodings["input_ids"],
                                  "attention_mask": test_encodings["attention_mask"],
                                  "labels": y_test.tolist()})



# Define model
model = BertForSequenceClassification.from_pretrained("UBC-NLP/ARBERTv2", num_labels=2,max_length=512)

# Define training arguments
training_args = TrainingArguments(
    per_device_train_batch_size=16,
    per_device_eval_batch_size=16,
    num_train_epochs=5,
    load_best_model_at_end=True,
    logging_dir='./logs',
    output_dir='./outputs',
    evaluation_strategy='steps',  # Add this line to match save strategy
    save_strategy='steps'
)

# Initialize Trainer
trainer = Trainer(
    model=model,
    args=training_args,
    train_dataset=train_dataset,
    eval_dataset=val_dataset,
)

# Train the model
trainer.train()

# Evaluate on test set
results = trainer.evaluate(test_dataset)
print(results)


Some weights of BertForSequenceClassification were not initialized from the model checkpoint at UBC-NLP/ARBERTv2 and are newly initialized: ['classifier.bias', 'classifier.weight']
You should probably TRAIN this model on a down-stream task to be able to use it for predictions and inference.
/usr/local/lib/python3.10/dist-packages/transformers/training_args.py:1474: FutureWarning: `evaluation_strategy` is deprecated and will be removed in version 4.46 of 🤗 Transformers. Use `eval_strategy` instead
  warnings.warn(


Some non-default generation parameters are set in the model config. These should go into a GenerationConfig file (https://huggingface.co/docs/transformers/generation_strategies#save-a-custom-decoding-strategy-with-your-model) instead. This warning will be raised to an exception in v4.41.
Non-default generation parameters: {'max_length': 512}
Some non-default generation parameters are set in the model config. These should go into a GenerationConfig file (https://huggingface.co/docs/transformers/generation_strategies#save-a-custom-decoding-strategy-with-your-model) instead. This warning will be raised to an exception in v4.41.
Non-default generation parameters: {'max_length': 512}
Some non-default generation parameters are set in the model config. These should go into a GenerationConfig file (https://huggingface.co/docs/transformers/generation_strategies#save-a-custom-decoding-strategy-with-your-model) instead. This warning will be raised to an exception in v4.41.
Non-default generation 

{'eval_loss': 0.06681051850318909, 'eval_runtime': 7.5769, 'eval_samples_per_second': 291.411, 'eval_steps_per_second': 18.213, 'epoch': 5.0}


In [ ]:
training_args

TrainingArguments(
_n_gpu=1,
accelerator_config={'split_batches': False, 'dispatch_batches': None, 'even_batches': True, 'use_seedable_sampler': True, 'non_blocking': False, 'gradient_accumulation_kwargs': None, 'use_configured_state': False},
adafactor=False,
adam_beta1=0.9,
adam_beta2=0.999,
adam_epsilon=1e-08,
auto_find_batch_size=False,
batch_eval_metrics=False,
bf16=False,
bf16_full_eval=False,
data_seed=None,
dataloader_drop_last=False,
dataloader_num_workers=0,
dataloader_persistent_workers=False,
dataloader_pin_memory=True,
dataloader_prefetch_factor=None,
ddp_backend=None,
ddp_broadcast_buffers=None,
ddp_bucket_cap_mb=None,
ddp_find_unused_parameters=None,
ddp_timeout=1800,
debug=[],
deepspeed=None,
disable_tqdm=False,
dispatch_batches=None,
do_eval=True,
do_predict=False,
do_train=False,
eval_accumulation_steps=None,
eval_delay=0,
eval_do_concat_batches=True,
eval_on_start=False,
eval_steps=500,
eval_strategy=steps,
evaluation_strategy=steps,
fp16=False,
fp16_backend=auto,
fp

In [ ]:
# prompt: now save the model trained by  the Trainer class

trainer.save_model("/content/drive/MyDrive/SDGs/Models/FinalBinaryArBERTv2_5Epochs_max512")


Some non-default generation parameters are set in the model config. These should go into a GenerationConfig file (https://huggingface.co/docs/transformers/generation_strategies#save-a-custom-decoding-strategy-with-your-model) instead. This warning will be raised to an exception in v4.41.
Non-default generation parameters: {'max_length': 512}


In [ ]:
tokenizer.save_pretrained("/content/drive/MyDrive/SDGs/Models/FinalBinaryArBERTv2_5Epochs_max512")

('/content/drive/MyDrive/SDGs/Models/FinalBinaryArBERTv2_5Epochs_max512/tokenizer_config.json',
 '/content/drive/MyDrive/SDGs/Models/FinalBinaryArBERTv2_5Epochs_max512/special_tokens_map.json',
 '/content/drive/MyDrive/SDGs/Models/FinalBinaryArBERTv2_5Epochs_max512/vocab.txt',
 '/content/drive/MyDrive/SDGs/Models/FinalBinaryArBERTv2_5Epochs_max512/added_tokens.json')

In [ ]:
# prompt: now load the saved model to model_loaded

from transformers import BertForSequenceClassification
model_loaded = BertForSequenceClassification.from_pretrained("/content/drive/MyDrive/SDGs/Models/FinalBinaryArBERTv2_5Epochs_max512")


In [ ]:
from transformers import Trainer, TrainingArguments
# Define training arguments
training_args = TrainingArguments(
    per_device_train_batch_size=16,
    per_device_eval_batch_size=16,
    num_train_epochs=5,
    load_best_model_at_end=True,
    logging_dir='./logs',
    output_dir='./outputs',
    evaluation_strategy='steps',  # Add this line to match save strategy
    save_strategy='steps'
)

# Initialize Trainer
trainer = Trainer(
    model=model_loaded,
    args=training_args,
    # ... other arguments such as train_dataset, eval_dataset, compute_metrics
)

/usr/local/lib/python3.10/dist-packages/transformers/training_args.py:1474: FutureWarning: `evaluation_strategy` is deprecated and will be removed in version 4.46 of 🤗 Transformers. Use `eval_strategy` instead
  warnings.warn(


#### T5

In [ ]:
!pip install simpletransformers==0.63.9

     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 250.5/250.5 kB 7.2 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 43.6/43.6 kB 6.2 MB/s eta 0:00:00
  Preparing metadata (setup.py) ... done
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 6.7/6.7 MB 75.0 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 8.6/8.6 MB 106.2 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 207.3/207.3 kB 28.6 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 289.2/289.2 kB 38.5 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 6.9/6.9 MB 110.4 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 83.0/83.0 kB 13.7 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 62.7/62.7 kB 9.8 MB/s eta 0:00:00
  Created wheel for seqeval: filename=seqeval-1.2.2-py3-none-any.whl size=16161 sha256=e27fb1ff75ca836c610da03e034140b667c45e239624085ec70230d18d1c94d5
  Stored in directory: /root/.cache/pip/wheels/1a/67/4a/ad4082dd7dfc30f2abfe4d8

In [ ]:
from simpletransformers.t5 import T5Model


import pandas as pd

X_train_downsampled = X_train_downsampled.reset_index(drop=True)
y_train_downsampled = y_train_downsampled.reset_index(drop=True)

train_df = pd.DataFrame({
    "prefix": ["binary classification: "] * len(X_train_downsampled),
    "input_text": X_train_downsampled.astype(str),  # Cast to string
    "target_text": y_train_downsampled.astype(str)  # Cast to string
})

eval_df = pd.DataFrame({
    "prefix": ["binary classification: "] * len(X_val),
    "input_text": X_val.astype(str),  # Cast to string
    "target_text": y_val.astype(str)  # Cast to string
})

model_args = {
    "max_seq_length": 128,
    "train_batch_size": 8,
    "eval_batch_size": 8,
    "num_train_epochs": 3,
    "evaluate_during_training": True,
    "evaluate_during_training_steps": 1000,
    "use_multiprocessing": False,
    "fp16": False,
    "save_steps": -1,
    "save_eval_checkpoints": False,
    "save_model_every_epoch": False,
    "overwrite_output_dir": True,
    "reprocess_input_data": True
}

#model = T5Model("t5", "google/mt5-base", args=model_args)
model = T5Model("t5", "UBC-NLP/AraT5v2-base-1024", args=model_args)


# Train the model
model.train_model(train_df, eval_data=eval_df)

# Evaluate the model
result = model.eval_model(eval_df)

/usr/local/lib/python3.10/dist-packages/huggingface_hub/file_download.py:1132: FutureWarning: `resume_download` is deprecated and will be removed in version 1.0.0. Downloads always resume when possible. If you want to force a new download, use `force_download=True`.
  warnings.warn(
/usr/local/lib/python3.10/dist-packages/huggingface_hub/utils/_token.py:89: UserWarning: 
The secret `HF_TOKEN` does not exist in your Colab secrets.
To authenticate with the Hugging Face Hub, create a token in your settings tab (https://huggingface.co/settings/tokens), set it as secret in your Google Colab and restart your session.
You will be able to reuse this secret in all of your notebooks.
Please note that authentication is recommended but still optional to access public models or datasets.
  warnings.warn(


config.json:   0%|          | 0.00/699 [00:00<?, ?B/s]

pytorch_model.bin:   0%|          | 0.00/1.47G [00:00<?, ?B/s]

generation_config.json:   0%|          | 0.00/142 [00:00<?, ?B/s]

tokenizer_config.json:   0%|          | 0.00/2.37k [00:00<?, ?B/s]

...

  0%|          | 0/2208 [00:00<?, ?it/s]

/usr/local/lib/python3.10/dist-packages/transformers/tokenization_utils_base.py:4072: FutureWarning: 
`prepare_seq2seq_batch` is deprecated and will be removed in version 5 of HuggingFace Transformers. Use the regular
`__call__` method to prepare your inputs and targets.

Here is a short example:

model_inputs = tokenizer(src_texts, text_target=tgt_texts, ...)

If you either need to use different keyword arguments for the source and target texts, you should do two calls like
this:

model_inputs = tokenizer(src_texts, ...)
labels = tokenizer(text_target=tgt_texts, ...)
model_inputs["labels"] = labels["input_ids"]

See the documentation of your specific tokenizer for more details on the specific arguments to the tokenizer of choice.
For a more complete example, see the implementation of `prepare_seq2seq_batch`.

  warnings.warn(formatted_warning, FutureWarning)
/usr/local/lib/python3.10/dist-packages/transformers/tokenization_utils_base.py:4072: FutureWarning: 
`prepare_seq2seq_batch` is

  0%|          | 0/2208 [00:00<?, ?it/s]

/usr/local/lib/python3.10/dist-packages/transformers/tokenization_utils_base.py:4072: FutureWarning: 
`prepare_seq2seq_batch` is deprecated and will be removed in version 5 of HuggingFace Transformers. Use the regular
`__call__` method to prepare your inputs and targets.

Here is a short example:

model_inputs = tokenizer(src_texts, text_target=tgt_texts, ...)

If you either need to use different keyword arguments for the source and target texts, you should do two calls like
this:

model_inputs = tokenizer(src_texts, ...)
labels = tokenizer(text_target=tgt_texts, ...)
model_inputs["labels"] = labels["input_ids"]

See the documentation of your specific tokenizer for more details on the specific arguments to the tokenizer of choice.
For a more complete example, see the implementation of `prepare_seq2seq_batch`.

  warnings.warn(formatted_warning, FutureWarning)
/usr/local/lib/python3.10/dist-packages/transformers/tokenization_utils_base.py:3946: UserWarning: `as_target_tokenizer` is depr

Running Evaluation:   0%|          | 0/276 [00:00<?, ?it/s]

In [ ]:
test_df = pd.DataFrame({
    "prefix": ["binary classification: "] * len(X_test),
    "input_text": X_test.astype(str),
    "target_text": y_test.astype(str)
})

predictions = model.predict(test_df["input_text"].tolist())

from sklearn.metrics import f1_score

macro_f1 = f1_score(y_test.astype(int), ([int(elm) for elm in predictions]), average='macro')
print("Macro F1 Score:", macro_f1)

Generating outputs:   0%|          | 0/276 [00:00<?, ?it/s]

/usr/local/lib/python3.10/dist-packages/transformers/tokenization_utils_base.py:4072: FutureWarning: 
`prepare_seq2seq_batch` is deprecated and will be removed in version 5 of HuggingFace Transformers. Use the regular
`__call__` method to prepare your inputs and targets.

Here is a short example:

model_inputs = tokenizer(src_texts, text_target=tgt_texts, ...)

If you either need to use different keyword arguments for the source and target texts, you should do two calls like
this:

model_inputs = tokenizer(src_texts, ...)
labels = tokenizer(text_target=tgt_texts, ...)
model_inputs["labels"] = labels["input_ids"]

See the documentation of your specific tokenizer for more details on the specific arguments to the tokenizer of choice.
For a more complete example, see the implementation of `prepare_seq2seq_batch`.

  warnings.warn(formatted_warning, FutureWarning)
/usr/local/lib/python3.10/dist-packages/transformers/generation/configuration_utils.py:563: UserWarning: `num_beams` is set to 1

Decoding outputs:   0%|          | 0/2208 [00:00<?, ?it/s]

Macro F1 Score: 0.9533430704316781


In [ ]:
model.model.save_pretrained('/content/drive/MyDrive/SDGs/Models/mT5_base_3Epochs/model1')
model.tokenizer.save_pretrained('/content/drive/MyDrive/SDGs/Models/mT5_base_3Epochs/model1')
model.config.save_pretrained('/content/drive/MyDrive/SDGs/Models/mT5_base_3Epochs/model1/')

In [ ]:
!cp -r "/content/outputs" "/content/drive/MyDrive/SDGs/Models/mT5_base_3Epochs"

### Evaluation

#### Test set

In [ ]:
from sklearn.metrics import accuracy_score, f1_score, recall_score,precision_score,roc_auc_score
import numpy as np



# Get the predictions for the test set
predictions = trainer.predict(test_dataset)

# Extract predicted labels
#predicted_labels = predictions.predictions.argmax(axis=1) # For BERT
predicted_labels=np.argmax(predictions.predictions, axis=1)

# Calculate accuracy
accuracy = accuracy_score(y_test, predicted_labels)

# Calculate F1 score(label 1)
f1_SDG = f1_score(y_test, predicted_labels)

# Calculate F1 score(label 0)
f1_NonSDG = f1_score(y_test, predicted_labels,pos_label=0)

# Calculate F1 score (micro)
f1_micro = f1_score(y_test, predicted_labels,average="micro")

# Calculate F1 score (micro)
f1_macro = f1_score(y_test, predicted_labels,average="macro")

#AOC score
macro_AOC_score=roc_auc_score(y_test, predicted_labels,average="macro")

print("Test Accuracy:", accuracy)
print("Test SDG F1 Score:", f1_SDG)
print("Test NonSDG F1 Score:", f1_NonSDG)
print("Test micro F1 Score:", f1_micro)
print("Test macro F1 Score:", f1_macro)
print("Test AUC score:", macro_AOC_score)


Test Accuracy: 0.9882246376811594
Test SDG F1 Score: 0.9931289640591966
Test NonSDG F1 Score: 0.9588607594936709
Test micro F1 Score: 0.9882246376811594
Test macro F1 Score: 0.9759948617764338
Test AUC score: 0.9863568010936433


In [ ]:
#bert-base seed 42 GPU T4 (Simple undersampling)
#Test Accuracy: 0.8573369565217391
#Test F1 Score: 0.9103840682788051

#ArbertV2 seed 42 GPU A100 (enhanced undersampling)
#Test Accuracy: 0.9923007246376812
#Test F1 Score: 0.9955133280548958

#ArbertV2 seed 24 GPU A100 (enhanced undersampling)
#Test Accuracy: 0.9864130434782609
#Test F1 Score: 0.9920550847457626

#ArbertV2 seed 2024 GPU A100 (enhanced undersampling)
#Test Accuracy: 0.9927536231884058
#Test F1 Score: 0.9957850368809273

#mT5-base seed 42 GPU A100 (enhanced undersampling)
#Test macro F1 Score: 0.9373958703178407

#AraT5-base-1024 seed 42 GPU A100 (enhanced undersampling)
#Test macro F1 Score: 0.9533430704316781


In [ ]:
result_test=pd.DataFrame({"predictions": predicted_labels,"Ground":y_test})

In [ ]:
result_test

predictions  Ground
2972             1       1
5408             0       0
13196            1       1
18691            1       1
38837            1       1
...            ...     ...
30987            1       1
40750            1       1
29695            1       1
38168            1       1
9163             1       1

[2208 rows x 2 columns]

#### Scraped sample

In [ ]:
Hespress=pd.read_pickle("/content/drive/MyDrive/SDGs/Data/Scrap/Hespress/Merged_Hespress.pkl")

In [ ]:
import numpy as np

Hespress200=Hespress.sample(n=200,random_state=42)
Hespress200.replace({'nan': np.nan}, regex=True,inplace=True)
Hespress200.replace(['None', 'nan'], np.nan,inplace=True)

Hespress200= Hespress200.dropna(subset=['Paragraphs'])
Hespress200['Paragraphs'] = Hespress200['Paragraphs'].astype(str)

In [ ]:
X_Sample=Hespress200['Paragraphs']

Sample_encodings = tokenizer(X_Sample.tolist(), truncation=True, padding=True,max_length=263)

Sample_dataset = Dataset.from_dict({"input_ids": Sample_encodings["input_ids"],
                                  "attention_mask": Sample_encodings["attention_mask"]})

In [ ]:
len(test_encodings["input_ids"][20])

263

In [ ]:
len(Sample_encodings["input_ids"][20])

263

In [ ]:
from sklearn.metrics import accuracy_score, f1_score




# Get the predictions for the test set
predictions = trainer.predict(Sample_dataset)

# Extract predicted labels
predicted_labels = predictions.predictions.argmax(axis=1)



In [ ]:
 import pandas as pd
 pd.Series(predicted_labels).value_counts(normalize=True)*100

0    80.0
1    20.0
Name: proportion, dtype: float64

In [ ]:
Hespress200_Predicted=pd.DataFrame({"Text":X_Sample,"predictions": predicted_labels})

In [ ]:
Hespress200_Predicted.to_csv("/content/drive/MyDrive/SDGs/Models/Predictions/Hespress200_Predicted.csv")

## Multi-class

In [ ]:
SDG_Data=Final_Data[Final_Data.sdg_binary==1]

In [ ]:
SDG_Data.sample(10)

sdg                                               text   Source  \
41673    3  ومنذ بداية القرن العشرين، تعرضت الشعوب الأصلية...     OSDG   
14810    3  تتطلب الوقاية من الأوبئة ومكافحتها من خلال برا...     OSDG   
11685    5  ومع ذلك، فإن مثل هذه الضريبة المنخفضة قد لا تك...     OSDG   
1970     8  فتحت المملكة العربية السعودية أبوابها لإقامة ا...  ChatGPT   
41318    9  الأداتان الرئيسيتان هما نظام تبادل البيانات ال...     OSDG   
615      4  تستعرض "وزارة التعليم" النموذج الجديد للتعلم ع...  ChatGPT   
6833    11  ومع ذلك، على المدى الطويل، ينبغي للنُهُج التي ...     OSDG   
3627     9  واجتذبت مشاريع النقل والتخزين غالبية هذه الأمو...     OSDG   
9579     7  ومن الأفضل لصانعي السياسات وصناع القرار أن يأخ...     OSDG   
2543     5  وقد تم تطويره في أوائل عام 2013 استجابة للبيان...     OSDG   

       sdg_binary  
41673           1  
14810           1  
11685           1  
1970            1  
41318           1  
615             1  
6833            1  
3627            1  
9579            1  
2543            1

In [ ]:
SDG_Data.Source.value_counts(normalize=True)*100

Source
OSDG       86.947942
ChatGPT    13.052058
Name: proportion, dtype: float64

### Data Split

In [ ]:
import pandas as pd
from sklearn.model_selection import train_test_split
from sklearn.utils import resample, shuffle


# Step 1: Data Splitting and Undersampling for Binary Classification (SDG vs. Non-SDG)

# Split the dataset into features (text) and labels (SDG)
X = SDG_Data['text']
y = SDG_Data['sdg']
S= SDG_Data['Source']


# Assuming 'y' and 'S' are your columns to stratify on
combined = y.astype(str) + '_' + S.astype(str)

# First split into train/test
X_train_temp, X_test, y_train_temp, y_test = train_test_split(X, combined, test_size=0.2, stratify=combined)

# Then split train set into train/validation
X_train, X_valid, y_train, y_valid = train_test_split(X_train_temp, y_train_temp, test_size=0.25, stratify=y_train_temp)


# # Assuming 'y' and 'S' are your columns to stratify on
# combined = y.astype(str) + '_' + S.astype(str)


# # Split the data into train, validation, and test sets
# X_train_val, X_val_test, y_train_val, y_val_test = train_test_split(X, y, test_size=0.15, random_state=42, stratify=combined)

# ##Create val and test sets
# X_val, X_test, y_val, y_test = train_test_split(X_val_test, y_val_test, test_size=0.5, random_state=42, stratify=y_val_test)




### Extract the original y's, subtract 1, and cast to integer
y_train = y_train.str.split('_', expand=True)[0].astype(int) - 1
y_valid = y_valid.str.split('_', expand=True)[0].astype(int) - 1
y_test = y_test.str.split('_', expand=True)[0].astype(int) - 1


### Training

In [ ]:
!rm -r "/content/outputs"

In [ ]:


# Initialize the BERT tokenizer
tokenizer = BertTokenizer.from_pretrained("UBC-NLP/ARBERTv2",model_max_length=512)

# # Tokenize texts and calculate number of tokens per text
# token_lengths = []
# for text in X_train_downsampled:
#     tokens = tokenizer.encode(text, add_special_tokens=True)
#     token_lengths.append(len(tokens))

# Calculate average number of tokens per text
# average_tokens = sum(token_lengths) / len(token_lengths)
# print(f"Average number of tokens per text: {average_tokens:.2f}")

# Convert labels to numerical values
# label_dict = {label: i for i, label in enumerate(Final_Data['sdg'].unique())}
# Final_Data['sdg'] = Final_Data['sdg'].map(label_dict)

# Split the data into training, validation, and test sets
# train_texts, val_test_texts, train_labels, val_test_labels = train_test_split(Final_Data['text'], Final_Data['sdg'], test_size=0.2, random_state=42, stratify=Final_Data['sdg'])
# val_texts, test_texts, val_labels, test_labels = train_test_split(val_test_texts, val_test_labels, test_size=0.5, random_state=42, stratify=val_test_labels)

# Tokenize the texts
train_encodings = tokenizer(X_train.tolist(), truncation=True, padding=True, max_length=512)
val_encodings = tokenizer(X_valid.tolist(), truncation=True, padding=True, max_length=512)
test_encodings = tokenizer(X_test.tolist(), truncation=True, padding=True, max_length=512)

# Create datasets
# train_dataset = Dataset.from_dict({key: val for key, val in train_encodings.items()}, labels=y_train_downsampled.tolist())
# val_dataset = Dataset.from_dict({key: val for key, val in val_encodings.items()}, labels= y_val.tolist())
# test_dataset = Dataset.from_dict({key: val for key, val in test_encodings.items()}, labels= y_test.tolist())

# Create the training dataset
train_dataset = Dataset.from_dict({"input_ids": train_encodings["input_ids"],
                                    "attention_mask": train_encodings["attention_mask"],
                                    "labels": y_train.tolist()})

# Create the validation dataset
val_dataset = Dataset.from_dict({"input_ids": val_encodings["input_ids"],
                                  "attention_mask": val_encodings["attention_mask"],
                                  "labels": y_valid.tolist()})

test_dataset = Dataset.from_dict({"input_ids": test_encodings["input_ids"],
                                  "attention_mask": test_encodings["attention_mask"],
                                  "labels": y_test.tolist()})



# Define model
model = BertForSequenceClassification.from_pretrained("UBC-NLP/ARBERTv2", num_labels=16, max_length=512)

# Define training arguments
training_args = TrainingArguments(
    per_device_train_batch_size=16,
    per_device_eval_batch_size=16,
    num_train_epochs=5,
     load_best_model_at_end=True,
    logging_dir='./logs',
    output_dir='./outputs',
    evaluation_strategy='steps',  # Add this line to match save strategy
    save_strategy='steps'
)

# Initialize Trainer
trainer = Trainer(
    model=model,
    args=training_args,
    train_dataset=train_dataset,
    eval_dataset=val_dataset,
)

# Train the model
trainer.train()

# Evaluate on test set
results = trainer.evaluate(test_dataset)
print(results)


/usr/local/lib/python3.10/dist-packages/huggingface_hub/utils/_token.py:89: UserWarning: 
The secret `HF_TOKEN` does not exist in your Colab secrets.
To authenticate with the Hugging Face Hub, create a token in your settings tab (https://huggingface.co/settings/tokens), set it as secret in your Google Colab and restart your session.
You will be able to reuse this secret in all of your notebooks.
Please note that authentication is recommended but still optional to access public models or datasets.
  warnings.warn(


tokenizer_config.json:   0%|          | 0.00/485 [00:00<?, ?B/s]

vocab.txt:   0%|          | 0.00/1.17M [00:00<?, ?B/s]

special_tokens_map.json:   0%|          | 0.00/125 [00:00<?, ?B/s]

config.json:   0%|          | 0.00/753 [00:00<?, ?B/s]

model.safetensors:   0%|          | 0.00/654M [00:00<?, ?B/s]

Some weights of BertForSequenceClassification were not initialized from the model checkpoint at UBC-NLP/ARBERTv2 and are newly initialized: ['classifier.bias', 'classifier.weight']
You should probably TRAIN this model on a down-stream task to be able to use it for predictions and inference.
/usr/local/lib/python3.10/dist-packages/transformers/training_args.py:1474: FutureWarning: `evaluation_strategy` is deprecated and will be removed in version 4.46 of 🤗 Transformers. Use `eval_strategy` instead
  warnings.warn(


Some non-default generation parameters are set in the model config. These should go into a GenerationConfig file (https://huggingface.co/docs/transformers/generation_strategies#save-a-custom-decoding-strategy-with-your-model) instead. This warning will be raised to an exception in v4.41.
Non-default generation parameters: {'max_length': 512}
Some non-default generation parameters are set in the model config. These should go into a GenerationConfig file (https://huggingface.co/docs/transformers/generation_strategies#save-a-custom-decoding-strategy-with-your-model) instead. This warning will be raised to an exception in v4.41.
Non-default generation parameters: {'max_length': 512}
Some non-default generation parameters are set in the model config. These should go into a GenerationConfig file (https://huggingface.co/docs/transformers/generation_strategies#save-a-custom-decoding-strategy-with-your-model) instead. This warning will be raised to an exception in v4.41.
Non-default generation 

{'eval_loss': 0.5516265630722046, 'eval_runtime': 17.2009, 'eval_samples_per_second': 294.637, 'eval_steps_per_second': 18.429, 'epoch': 5.0}


In [ ]:
trainer.save_model("/content/drive/MyDrive/SDGs/Models/FinalMultiClassArBERTv2_5Epochs_max512")
tokenizer.save_pretrained("/content/drive/MyDrive/SDGs/Models/FinalMultiClassArBERTv2_5Epochs_max512")

Some non-default generation parameters are set in the model config. These should go into a GenerationConfig file (https://huggingface.co/docs/transformers/generation_strategies#save-a-custom-decoding-strategy-with-your-model) instead. This warning will be raised to an exception in v4.41.
Non-default generation parameters: {'max_length': 512}


('/content/drive/MyDrive/SDGs/Models/FinalMultiClassArBERTv2_5Epochs_max512/tokenizer_config.json',
 '/content/drive/MyDrive/SDGs/Models/FinalMultiClassArBERTv2_5Epochs_max512/special_tokens_map.json',
 '/content/drive/MyDrive/SDGs/Models/FinalMultiClassArBERTv2_5Epochs_max512/vocab.txt',
 '/content/drive/MyDrive/SDGs/Models/FinalMultiClassArBERTv2_5Epochs_max512/added_tokens.json')

#### AraBART

In [ ]:
from transformers import BartTokenizer, BartForSequenceClassification, Trainer, TrainingArguments,AutoTokenizer
from datasets import Dataset
import pandas as pd



# Initialize the BART tokenizer
tokenizer = AutoTokenizer.from_pretrained("eslamxm/AraBART-finetuned-ar-wikilingua")

# Tokenize the texts
train_encodings = tokenizer(X_train.tolist(), truncation=True, padding=True)
val_encodings = tokenizer(X_valid.tolist(), truncation=True, padding=True)
test_encodings = tokenizer(X_test.tolist(), truncation=True, padding=True)

# Create datasets
train_dataset = Dataset.from_dict({
    "input_ids": train_encodings["input_ids"],
    "attention_mask": train_encodings["attention_mask"],
    "labels": y_train.tolist()
})

val_dataset = Dataset.from_dict({
    "input_ids": val_encodings["input_ids"],
    "attention_mask": val_encodings["attention_mask"],
    "labels": y_valid.tolist()
})

test_dataset = Dataset.from_dict({
    "input_ids": test_encodings["input_ids"],
    "attention_mask": test_encodings["attention_mask"],
    "labels": y_test.tolist()
})

# Define the model
model = BartForSequenceClassification.from_pretrained("eslamxm/AraBART-finetuned-ar-wikilingua", num_labels=16)

# Define training arguments
training_args = TrainingArguments(
    per_device_train_batch_size=16,
    per_device_eval_batch_size=16,
    num_train_epochs=5,
    load_best_model_at_end=True,
    logging_dir='./logs',
    output_dir='./outputs',
         evaluation_strategy='steps',  # Add this line to match save strategy
    save_strategy='steps'
)

# Initialize the Trainer
trainer = Trainer(
    model=model,
    args=training_args,
    train_dataset=train_dataset,
    eval_dataset=val_dataset,
)

# Train the model
trainer.train()

# Evaluate on the test set
results = trainer.evaluate(test_dataset)
print(results)


Asking to truncate to max_length but no maximum length is provided and the model has no predefined maximum length. Default to no truncation.
You are using a model of type mbart to instantiate a model of type bart. This is not supported for all configurations of models and can yield errors.
Some weights of BartForSequenceClassification were not initialized from the model checkpoint at eslamxm/AraBART-finetuned-ar-wikilingua and are newly initialized: ['classification_head.dense.bias', 'classification_head.dense.weight', 'classification_head.out_proj.bias', 'classification_head.out_proj.weight']
You should probably TRAIN this model on a down-stream task to be able to use it for predictions and inference.
/usr/local/lib/python3.10/dist-packages/transformers/training_args.py:1474: FutureWarning: `evaluation_strategy` is deprecated and will be removed in version 4.46 of 🤗 Transformers. Use `eval_strategy` instead
  warnings.warn(


Some non-default generation parameters are set in the model config. These should go into a GenerationConfig file (https://huggingface.co/docs/transformers/generation_strategies#save-a-custom-decoding-strategy-with-your-model) instead. This warning will be raised to an exception in v4.41.
Non-default generation parameters: {'early_stopping': True, 'num_beams': 4, 'no_repeat_ngram_size': 3, 'forced_eos_token_id': 2}
Some non-default generation parameters are set in the model config. These should go into a GenerationConfig file (https://huggingface.co/docs/transformers/generation_strategies#save-a-custom-decoding-strategy-with-your-model) instead. This warning will be raised to an exception in v4.41.
Non-default generation parameters: {'early_stopping': True, 'num_beams': 4, 'no_repeat_ngram_size': 3, 'forced_eos_token_id': 2}
Some non-default generation parameters are set in the model config. These should go into a GenerationConfig file (https://huggingface.co/docs/transformers/generatio

{'eval_loss': 1.202429175376892, 'eval_runtime': 21.8544, 'eval_samples_per_second': 231.898, 'eval_steps_per_second': 14.505, 'epoch': 5.0}


### Evaluation

In [ ]:
!cp -r "/content/outputs" "/content/drive/MyDrive/SDGs/Models/MultiClass_A100_5Epochs_Arbert"

In [ ]:
from sklearn.metrics import accuracy_score, f1_score, recall_score,precision_score,roc_auc_score
import numpy as np



# Get the predictions for the test set
predictions = trainer.predict(test_dataset)

# Extract predicted labels
predicted_labels = predictions.predictions.argmax(axis=1) # For BERT
#predicted_labels=np.argmax(predictions.predictions, axis=1)

# Calculate accuracy
accuracy = accuracy_score(y_test, predicted_labels)


# Calculate F1 score (micro)
f1_micro = f1_score(y_test, predicted_labels,average="micro")

# Calculate F1 score (micro)
f1_macro = f1_score(y_test, predicted_labels,average="macro")

# Calculate F1 score (Weighted)
f1_macro_W = f1_score(y_test, predicted_labels,average="weighted")

#AOC score
#macro_AOC_score=roc_auc_score(y_test, predicted_labels,average="macro",multi_class='ovo')

print("Test Accuracy:", accuracy)

print("Test micro F1 Score:", f1_micro)
print("Test macro F1 Score:", f1_macro)
print("Test Weighted F1 Score:", f1_macro_W)
#print("Test AUC score:", macro_AOC_score)


Test Accuracy: 0.8772691397000789
Test micro F1 Score: 0.8772691397000789
Test macro F1 Score: 0.8558380601404871
Test Weighted F1 Score: 0.8778897574870056


In [ ]:
#### 10 epochs


from sklearn.metrics import accuracy_score, f1_score, recall_score,precision_score,roc_auc_score
import numpy as np



# Get the predictions for the test set
predictions = trainer.predict(test_dataset)

# Extract predicted labels
predicted_labels = predictions.predictions.argmax(axis=1) # For BERT
#predicted_labels=np.argmax(predictions.predictions, axis=1)

# Calculate accuracy
accuracy = accuracy_score(y_test, predicted_labels)


# Calculate F1 score (micro)
f1_micro = f1_score(y_test, predicted_labels,average="micro")

# Calculate F1 score (micro)
f1_macro = f1_score(y_test, predicted_labels,average="macro")

# Calculate F1 score (Weighted)
f1_macro_W = f1_score(y_test, predicted_labels,average="weighted")

#AOC score
#macro_AOC_score=roc_auc_score(y_test, predicted_labels,average="macro",multi_class='ovo')

print("Test Accuracy:", accuracy)

print("Test micro F1 Score:", f1_micro)
print("Test macro F1 Score:", f1_macro)
print("Test Weighted F1 Score:", f1_macro_W)
#print("Test AUC score:", macro_AOC_score)


Test Accuracy: 0.8498421468034728
Test micro F1 Score: 0.8498421468034728
Test macro F1 Score: 0.828650771418186
Test Weighted F1 Score: 0.8503662521758165


In [ ]:
# Get the predicted probabilities for the test set
prediction_probabilities = trainer.predict(test_dataset).predictions

# Apply softmax to convert logits to probabilities
import torch
import torch.nn.functional as F
prediction_probabilities = F.softmax(torch.tensor(prediction_probabilities), dim=1).numpy()

# Calculate ROC AUC score (macro-averaged one-vs-one)
ovo_AOC_score = roc_auc_score(y_test, prediction_probabilities, multi_class='ovo')
ovr_AOC_score = roc_auc_score(y_test, prediction_probabilities, multi_class='ovr')
print("Test ovo AUC score:", ovo_AOC_score)
print("Test ovr AUC score:", ovr_AOC_score)

Test ovo AUC score: 0.9802421420536442
Test ovr AUC score: 0.982752220651779


In [ ]:
# 10 epochs


# Get the predicted probabilities for the test set
prediction_probabilities = trainer.predict(test_dataset).predictions

# Apply softmax to convert logits to probabilities
import torch
import torch.nn.functional as F
prediction_probabilities = F.softmax(torch.tensor(prediction_probabilities), dim=1).numpy()

# Calculate ROC AUC score (macro-averaged one-vs-one)
ovo_AOC_score = roc_auc_score(y_test, prediction_probabilities, multi_class='ovo')
ovr_AOC_score = roc_auc_score(y_test, prediction_probabilities, multi_class='ovr')
print("Test ovo AUC score:", ovo_AOC_score)
print("Test ovr AUC score:", ovr_AOC_score)

Test ovo AUC score: 0.9722481870165417
Test ovr AUC score: 0.9754126995133388


#### AraBART

In [ ]:
# Get predictions
predictions = trainer.predict(test_dataset)

# Access the logits from the predictions output (adjust index if needed)
logits = predictions.predictions[0]

# Reshape logits if necessary (adjust dimensions as needed)
logits = logits.reshape(-1, 16)  # Replace num_classes with the actual number

# Apply softmax to get probabilities
probs = torch.softmax(torch.tensor(logits), dim=-1)

# Get the predicted class
preds = torch.argmax(probs, dim=-1).numpy()

In [ ]:
# Calculate accuracy
accuracy = accuracy_score(y_test, preds)


# Calculate F1 score (micro)
f1_micro = f1_score(y_test, preds,average="micro")

# Calculate F1 score (micro)
f1_macro = f1_score(y_test, preds,average="macro")

# Calculate F1 score (Weighted)
f1_macro_W = f1_score(y_test, preds,average="weighted")

#AOC score
#macro_AOC_score=roc_auc_score(y_test, preds,average="macro",multi_class='ovo')

print("Test Accuracy:", accuracy)

print("Test micro F1 Score:", f1_micro)
print("Test macro F1 Score:", f1_macro)
print("Test Weighted F1 Score:", f1_macro_W)
#print("Test AUC score:", macro_AOC_score)

Test Accuracy: 0.6728492501973165
Test micro F1 Score: 0.6728492501973165
Test macro F1 Score: 0.5684494764500512
Test Weighted F1 Score: 0.6553619401927359


In [ ]:
# A100 5 Epochs bs16
# Test Accuracy: 0.8749013417521705
# Test micro F1 Score: 0.8749013417521705
# Test macro F1 Score: 0.8569543276822498
# Test Weighted F1 score: 0.8749054860171084
# Test macro AUC score: 0.9802421420536442 (ovo)

#A100 10 epochs bs 16
#Test Accuracy: 0.8498421468034728
#Test micro F1 Score: 0.8498421468034728
#Test macro F1 Score: 0.828650771418186
#Test Weighted F1 Score: 0.8503662521758165

In [ ]:
Hespress200Predicted=pd.read_csv("/content/drive/MyDrive/SDGs/Models/Predictions/Hespress200_Predicted.csv")

In [ ]:
Hespress200Predicted.head(10)

Unnamed: 0                                               Text  predictions
0      416525  بعدما كشفت وسائل إعلام مغربية عن وقوع سرقة تما...            0
1      404041  أسباب عديدة تكمن وراء اتخاذ المغرب قرار العودة...            0
2       24740  مع استمرار عدد الوفيات الناجمة عن فيروس كوفيد-...            0
3       75517  أنهى فريق الجيش الملكي الموسم الرياضي 2011-201...            0
4      266433  أحجم تنسيق حركة 20 فبراير الناظورية عن النزول ...            0
5      231728  ارتقى المنتخب الوطني المغربي للدراجات إلى الصف...            0
6      320652  دهس قطار لنقل الفوسفاط مساء أمس الأحد باقليم خ...            0
7      395027  دقّ كل من المركز الاستشفائي محمد السادس ولجنة ...            1
8      384827  تبدو محطات موزعي البنزين بالمغرب، في مختلف مدن...            0
9       83590  قال مولاي الحسن الداكي، الوكيل العام للملك لدى...            1

In [ ]:
Hespress_SDG=Hespress200Predicted[Hespress200Predicted.predictions==1]

In [ ]:
len(Hespress_SDG)

15

In [ ]:
# Initialize the BERT tokenizer
tokenizer = BertTokenizer.from_pretrained("UBC-NLP/ARBERTv2")

X_Sample=Hespress_SDG['Text']

Sample_encodings = tokenizer(X_Sample.tolist(), truncation=True, padding=True,max_length=263)

Sample_dataset = Dataset.from_dict({"input_ids": Sample_encodings["input_ids"],
                                  "attention_mask": Sample_encodings["attention_mask"]})

In [ ]:
from sklearn.metrics import accuracy_score, f1_score




# Get the predictions for the test set
predictions = trainer.predict(Sample_dataset)

# Extract predicted labels
predicted_labels = predictions.predictions.argmax(axis=1)

In [ ]:
predicted_labels

array([ 2, 15,  0, 10, 15,  4,  3,  1, 15,  9,  9, 10,  2,  0,  2])

In [ ]:
# prompt: create a dictionnaty to map between SDG numbers and their names

sdg_dict = {
    0: "No Poverty",
    1: "Zero Hunger",
    2: "Good Health and Well-being",
    3: "Quality Education",
    4: "Gender Equality",
    5: "Clean Water and Sanitation",
    6: "Affordable and Clean Energy",
    7: "Decent Work and Economic Growth",
    8: "Industry, Innovation and Infrastructure",
    9: "Reduced Inequalities",
    10: "Sustainable Cities and Communities",
    11: "Responsible Consumption and Production",
    12: "Climate Action",
    13: "Life Below Water",
    14: "Life on Land",
    15: "Peace and Justice Strong Institutions",
    16: "Partnerships for the Goals"
}


In [ ]:
# prompt: Map predicted_labels to sdg names using sdg_dict, then add it to Hespress_SDG Dataframe as a column named prediction_sdg

Hespress_SDG["prediction_sdg"] = [sdg_dict[predicted_label] for predicted_label in predicted_labels]


<ipython-input-46-d3203d86f641>:3: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  Hespress_SDG["prediction_sdg"] = [sdg_dict[predicted_label] for predicted_label in predicted_labels]


In [ ]:
Hespress_SDG

Unnamed: 0                                               Text  \
7        395027  دقّ كل من المركز الاستشفائي محمد السادس ولجنة ...   
9         83590  قال مولاي الحسن الداكي، الوكيل العام للملك لدى...   
11        68807  منحت إدارة مؤسسة التعاون الوطني، اليوم الجمعة،...   
27       302774  أشرف سعيد الرحموني، رئيس المجلس الإقليمي للناظ...   
40       162031  ( ليس الشعب بحاجة إلى أن نتكلم عن حقوقه وحريته...   
41       364715  لا شك أن كل مسلم، بل حتى غير المسلمين من المنت...   
47       433082  “إن التلامذة المترجمين يتعلمون في المدرسة العل...   
52       429253  قال أنطونيو غوتيريتش، الأمين العام للأمم المتح...   
54       144747  بخلاف آراء ذهبت إلى أن استقلال النيابة العامة ...   
77       436954  المشاركون الذي حجوا من كل مقاطعات مراكش، المنت...   
82       434964  “الخبر” نقلت أن أجور الموظفين وتكاليف صندوق ال...   
90       119780  احتضنت مدينة الداخلة، الإثنين، حفل رفع اللواء ...   
92       313574  بتنسيق بين مندوبية وزارة الصحة بإقليم أزيلال و...   
98       300148  قال أنطونيو غوتيريس، الأمين العام للأمم المتحد...   
103      232788  تتراجع فعالية الجرعة المعززة من لقاحي “فايزر” ...   

     predictions                         prediction_sdg  
7              1             Good Health and Well-being  
9              1  Peace and Justice Strong Institutions  
11             1                             No Poverty  
27             1     Sustainable Cities and Communities  
40             1  Peace and Justice Strong Institutions  
41             1                        Gender Equality  
47             1                      Quality Education  
52             1                            Zero Hunger  
54             1  Peace and Justice Strong Institutions  
77             1                   Reduced Inequalities  
82             1                   Reduced Inequalities  
90             1     Sustainable Cities and Communities  
92             1             Good Health and Well-being  
98             1                             No Poverty  
103            1             Good Health and Well-being

In [ ]:
Hespress_SDG.to_csv("/content/drive/MyDrive/SDGs/Models/Predictions/MultiClass_Hespress15.csv")

In [ ]:
from transformers import AutoModelForSequenceClassification
model = AutoModelForSequenceClassification.from_pretrained('/content/drive/MyDrive/SDGs/Models/MultiClass_A100_5Epochs_Arbert/checkpoint-500')

In [ ]:
from transformers import Trainer, TrainingArguments
# Define training arguments
training_args = TrainingArguments(
    per_device_train_batch_size=16,
    per_device_eval_batch_size=16,
    num_train_epochs=5,
    logging_dir='./logs',
    output_dir='./outputs'
)

# Initialize Trainer
trainer = Trainer(
    model=model,
    args=training_args,
    # ... other arguments such as train_dataset, eval_dataset, compute_metrics
)



In [ ]:
training_args

TrainingArguments(
_n_gpu=1,
accelerator_config={'split_batches': False, 'dispatch_batches': None, 'even_batches': True, 'use_seedable_sampler': True, 'non_blocking': False, 'gradient_accumulation_kwargs': None},
adafactor=False,
adam_beta1=0.9,
adam_beta2=0.999,
adam_epsilon=1e-08,
auto_find_batch_size=False,
batch_eval_metrics=False,
bf16=False,
bf16_full_eval=False,
data_seed=None,
dataloader_drop_last=False,
dataloader_num_workers=0,
dataloader_persistent_workers=False,
dataloader_pin_memory=True,
dataloader_prefetch_factor=None,
ddp_backend=None,
ddp_broadcast_buffers=None,
ddp_bucket_cap_mb=None,
ddp_find_unused_parameters=None,
ddp_timeout=1800,
debug=[],
deepspeed=None,
disable_tqdm=False,
dispatch_batches=None,
do_eval=False,
do_predict=False,
do_train=False,
eval_accumulation_steps=None,
eval_delay=0,
eval_do_concat_batches=True,
eval_steps=None,
eval_strategy=no,
evaluation_strategy=None,
fp16=False,
fp16_backend=auto,
fp16_full_eval=False,
fp16_opt_level=O1,
fsdp=[],
fsdp_c

In [ ]:
from sklearn.metrics import accuracy_score, f1_score




# Get the predictions for the test set
predictions = trainer.predict(Sample_dataset)

# Extract predicted labels
predicted_labels = predictions.predictions.argmax(axis=1)

In [ ]:
predicted_labels
array([ 2, 15,  0, 10, 15,  4,  3,  1, 15,  9,  9, 10,  2,  0,  2])

array([ 2,  4,  4, 10, 15,  4,  3,  1, 15,  7,  7,  5,  2,  0,  2])